In [ ]:
import boto3
import sagemaker
import json
import os
from utils import get_aws_profile_name, get_aws_iam_role

LOCAL_EXECUTION = True

if LOCAL_EXECUTION:
    sess = boto3.Session(profile_name=get_aws_profile_name())
    sm = sess.client("sagemaker")
    iam = sess.client('iam')
    role = iam.get_role(RoleName=get_aws_iam_role())['Role']['Arn']
else:
    sess = boto3.Session()
    sm = sess.client("sagemaker")
    role = sagemaker.get_execution_role()

sagemaker_session = sagemaker.Session(boto_session=sess)
bucket = sagemaker_session.default_bucket()
prefix = "model-monitor-bring-your-own-model/"
region = sess.region_name

In [ ]:
%load_ext autoreload
%autoreload 2

# First run 
Run the following if it is the first time you are running code in this repo and want to create the base dataset and baselines.

In [ ]:
%%bash
# The following command will create the config file where the code will be saving some intermediate information.
# Once run, open the fule and under the aws-settings add your "profilename" and "executionrole" that you want to use when running this example

# echo $'[aws-settings] \n\n[BASELINES] \n\n[DATASETS]' > config.ini


In [ ]:
# %run prep.py
# %run 01_create_baselines.ipynb

In [ ]:
from utils import get_baseline_uri
from botocore.exceptions import ClientError

def print_violations(type:str)->None:
    print("violations ",type )

    violations_uri = get_baseline_uri(type)
    try:
        violations = json.loads(sagemaker.s3.S3Downloader().read_file(violations_uri, sagemaker_session=sagemaker_session))

        print(json.dumps(violations, indent=4))
        print()
    except ClientError as ex:
        if ex.response['Error']['Code'] == 'NoSuchKey':
            print("No violation file found for ", type)
    

In [ ]:
import generate_altered
from generate_altered import TransformsEnum
from sagemaker.experiments.run import Run
from datetime import datetime
from utils import save_trial_name


def run_full_analysis(transform: TransformsEnum = TransformsEnum.DEFAULT):
    experiment_name = "model-monitor-byom"
    run_name = transform.__name__.replace("_","-") + "-" + datetime.now().strftime("%Y-%m-%d-%H-%M")

    with Run(experiment_name=experiment_name, sagemaker_session=sagemaker_session, run_name=run_name) as run:

        generate_altered.main(transform)
        
        %run 02_data_quality_checks.ipynb
        %run 03_model_quality_checks.ipynb
        %run 04_model_explainability_checks.ipynb
        %run 04_model_bias_checks.ipynb

        print_violations('data-quality-violoations')
        print_violations('model-quality-violoations')
        print_violations('model-bias-violoations')
        print_violations('model-explainability-violoations')

        run.log_parameters({
            "tranform_used": transform.__name__,
            "data-quality-violoations": get_baseline_uri("data-quality-violoations"),
            "model-quality-violoations": get_baseline_uri("model-quality-violoations"),
            "model-bias-violoations": get_baseline_uri("model-bias-violoations"),
            "model-explainability-violoations": get_baseline_uri("model-explainability-violoations"),
        })

        save_trial_name(transform.__name__.replace("_","-"), experiment_name+"-"+run_name)

## Alter & Run 
Alter data data, 
and then run drift checks

In [ ]:
# import generate_altered
# generate_altered.main()


In [ ]:
# %run 02_data_quality_checks.ipynb
# %run 03_model_quality_checks.ipynb
# %run 04_model_explainability_checks.ipynb
# %run 04_model_bias_checks.ipynb

### Scenario - Concept Drift

In [24]:
run_full_analysis(TransformsEnum.CONCEPT_DRIFT)


2023-02-10 13:37:17,385 Endpoint is in service after 241 seconds
2023-02-10 13:37:17,385 Endpoint ready.
2023-02-10 13:37:17,385 ======================================
2023-02-10 13:37:17,385 Calculating post-training bias metrics
2023-02-10 13:37:17,385 ======================================
2023-02-10 13:37:17,385 Getting predictions from the endpoint
2023-02-10 13:37:17,840 We assume a prediction above 0.500 indicates 1 and below or equal indicates 0.
2023-02-10 13:37:17,841 Column credit_risk with data uniqueness fraction 0.002 is classifed as a CATEGORICAL column
2023-02-10 13:37:17,843 Column foreign_worker with data uniqueness fraction 0.002 is classifed as a CATEGORICAL column
/usr/local/lib/python3.9/site-packages/smclarify/bias/report.py:469: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  df = df.drop(facet_column.name, 1)
2023-02-10 13:37:17,845 Column credit_risk with data uniqueness frac

### Scenario - Label Drift

In [25]:
run_full_analysis(TransformsEnum.LABEL_DRIFT)

/Users/schinasg/opt/anaconda3/envs/mm-byom/lib/python3.8/site-packages/sklearn/compose/_column_transformer.py:437: FutureWarning: Given feature/column names or counts do not match the ones for the data given during fit. This will fail from v0.24.
  warnings.warn("Given feature/column names or counts do not match "
INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-monitor-byom-2023-02-10-13-38-00-786



Job Name:  model-monitor-byom-2023-02-10-13-38-00-786
Inputs:  [{'InputName': 'baseline_dataset_input', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-quality/modified_input_data/data_quality_modified_data.csv', 'LocalPath': '/opt/ml/processing/input/baseline_dataset_input', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'constraints', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-quality/baseline_results/constraints.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'baseline', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-qu

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-monitor-byom-2023-02-10-13-43-52-636



Job Name:  model-monitor-byom-2023-02-10-13-43-52-636
Inputs:  [{'InputName': 'baseline_dataset_input', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality/input_data/model_quality_modified_data.csv', 'LocalPath': '/opt/ml/processing/input/baseline_dataset_input', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'constraints', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality/baseline_results/constraints.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'baseline', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-explainability-byom-2023-02-10-13-50-14-327



Job Name:  model-explainability-byom-2023-02-10-13-50-14-327
Inputs:  [{'InputName': 'analysis_file', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/baseline_results/analysis.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'analysis_config', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/baseline_results/analysis_config.json', 'LocalPath': '/opt/ml/processing/input/config', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'dataset', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/i

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-bias-byom-2023-02-10-14-02-22-447



Job Name:  model-bias-byom-2023-02-10-14-02-22-447
Inputs:  [{'InputName': 'analysis_file', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/baseline_results/analysis.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'analysis_config', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/baseline_results/analysis_config.json', 'LocalPath': '/opt/ml/processing/input/config', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'dataset', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/input_data/model_bias_modified_data.csv',

### Scenario - Feature Drift

In [26]:
run_full_analysis(TransformsEnum.FEATURE_DRIFT)

/Users/schinasg/opt/anaconda3/envs/mm-byom/lib/python3.8/site-packages/sklearn/compose/_column_transformer.py:437: FutureWarning: Given feature/column names or counts do not match the ones for the data given during fit. This will fail from v0.24.
  warnings.warn("Given feature/column names or counts do not match "
INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-monitor-byom-2023-02-10-14-13-11-027



Job Name:  model-monitor-byom-2023-02-10-14-13-11-027
Inputs:  [{'InputName': 'baseline_dataset_input', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-quality/modified_input_data/data_quality_modified_data.csv', 'LocalPath': '/opt/ml/processing/input/baseline_dataset_input', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'constraints', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-quality/baseline_results/constraints.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'baseline', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-qu

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-monitor-byom-2023-02-10-14-19-32-919



Job Name:  model-monitor-byom-2023-02-10-14-19-32-919
Inputs:  [{'InputName': 'baseline_dataset_input', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality/input_data/model_quality_modified_data.csv', 'LocalPath': '/opt/ml/processing/input/baseline_dataset_input', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'constraints', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality/baseline_results/constraints.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'baseline', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-explainability-byom-2023-02-10-14-25-25-507



Job Name:  model-explainability-byom-2023-02-10-14-25-25-507
Inputs:  [{'InputName': 'analysis_file', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/baseline_results/analysis.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'analysis_config', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/baseline_results/analysis_config.json', 'LocalPath': '/opt/ml/processing/input/config', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'dataset', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/i

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-bias-byom-2023-02-10-14-35-29-135



Job Name:  model-bias-byom-2023-02-10-14-35-29-135
Inputs:  [{'InputName': 'analysis_file', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/baseline_results/analysis.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'analysis_config', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/baseline_results/analysis_config.json', 'LocalPath': '/opt/ml/processing/input/config', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'dataset', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/input_data/model_bias_modified_data.csv',

### Scenario - Feature Drift due to systematic error

In [27]:
run_full_analysis(TransformsEnum.FEATURE_DRIFT_SYSTEMATIC)

/Users/schinasg/opt/anaconda3/envs/mm-byom/lib/python3.8/site-packages/sklearn/compose/_column_transformer.py:437: FutureWarning: Given feature/column names or counts do not match the ones for the data given during fit. This will fail from v0.24.
  warnings.warn("Given feature/column names or counts do not match "
INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-monitor-byom-2023-02-10-14-45-10-524



Job Name:  model-monitor-byom-2023-02-10-14-45-10-524
Inputs:  [{'InputName': 'baseline_dataset_input', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-quality/modified_input_data/data_quality_modified_data.csv', 'LocalPath': '/opt/ml/processing/input/baseline_dataset_input', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'constraints', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-quality/baseline_results/constraints.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'baseline', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-qu

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-monitor-byom-2023-02-10-14-51-01-822



Job Name:  model-monitor-byom-2023-02-10-14-51-01-822
Inputs:  [{'InputName': 'baseline_dataset_input', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality/input_data/model_quality_modified_data.csv', 'LocalPath': '/opt/ml/processing/input/baseline_dataset_input', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'constraints', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality/baseline_results/constraints.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'baseline', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-explainability-byom-2023-02-10-14-56-54-558



Job Name:  model-explainability-byom-2023-02-10-14-56-54-558
Inputs:  [{'InputName': 'analysis_file', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/baseline_results/analysis.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'analysis_config', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/baseline_results/analysis_config.json', 'LocalPath': '/opt/ml/processing/input/config', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'dataset', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/i

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-bias-byom-2023-02-10-15-06-58-310



Job Name:  model-bias-byom-2023-02-10-15-06-58-310
Inputs:  [{'InputName': 'analysis_file', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/baseline_results/analysis.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'analysis_config', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/baseline_results/analysis_config.json', 'LocalPath': '/opt/ml/processing/input/config', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'dataset', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/input_data/model_bias_modified_data.csv',

### Scenario - Explainability Drift

In [28]:
run_full_analysis(TransformsEnum.EXPLAINABILITY_DRIFT)

/Users/schinasg/opt/anaconda3/envs/mm-byom/lib/python3.8/site-packages/sklearn/compose/_column_transformer.py:437: FutureWarning: Given feature/column names or counts do not match the ones for the data given during fit. This will fail from v0.24.
  warnings.warn("Given feature/column names or counts do not match "
INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-monitor-byom-2023-02-10-15-17-10-039



Job Name:  model-monitor-byom-2023-02-10-15-17-10-039
Inputs:  [{'InputName': 'baseline_dataset_input', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-quality/modified_input_data/data_quality_modified_data.csv', 'LocalPath': '/opt/ml/processing/input/baseline_dataset_input', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'constraints', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-quality/baseline_results/constraints.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'baseline', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-qu

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-monitor-byom-2023-02-10-15-23-01-806



Job Name:  model-monitor-byom-2023-02-10-15-23-01-806
Inputs:  [{'InputName': 'baseline_dataset_input', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality/input_data/model_quality_modified_data.csv', 'LocalPath': '/opt/ml/processing/input/baseline_dataset_input', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'constraints', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality/baseline_results/constraints.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'baseline', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-explainability-byom-2023-02-10-15-28-56-990



Job Name:  model-explainability-byom-2023-02-10-15-28-56-990
Inputs:  [{'InputName': 'analysis_file', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/baseline_results/analysis.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'analysis_config', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/baseline_results/analysis_config.json', 'LocalPath': '/opt/ml/processing/input/config', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'dataset', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/i

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-bias-byom-2023-02-10-15-39-29-117



Job Name:  model-bias-byom-2023-02-10-15-39-29-117
Inputs:  [{'InputName': 'analysis_file', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/baseline_results/analysis.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'analysis_config', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/baseline_results/analysis_config.json', 'LocalPath': '/opt/ml/processing/input/config', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'dataset', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/input_data/model_bias_modified_data.csv',

### Scenario - Bias Drift

In [29]:
run_full_analysis(TransformsEnum.BIAS_DRIFT)

/Users/schinasg/opt/anaconda3/envs/mm-byom/lib/python3.8/site-packages/sklearn/compose/_column_transformer.py:437: FutureWarning: Given feature/column names or counts do not match the ones for the data given during fit. This will fail from v0.24.
  warnings.warn("Given feature/column names or counts do not match "
/Users/schinasg/Documents/GitLab/byom_model_monitor/generate_altered.py:141: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["foreign_worker"] = df["foreign_worker"].apply(lambda x: 5*[x] if (x == 1) else x)
INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-monitor-byom-2023-02-10-15-50-40-632



Job Name:  model-monitor-byom-2023-02-10-15-50-40-632
Inputs:  [{'InputName': 'baseline_dataset_input', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-quality/modified_input_data/data_quality_modified_data.csv', 'LocalPath': '/opt/ml/processing/input/baseline_dataset_input', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'constraints', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-quality/baseline_results/constraints.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'baseline', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/data-qu

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-monitor-byom-2023-02-10-15-57-03-249



Job Name:  model-monitor-byom-2023-02-10-15-57-03-249
Inputs:  [{'InputName': 'baseline_dataset_input', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality/input_data/model_quality_modified_data.csv', 'LocalPath': '/opt/ml/processing/input/baseline_dataset_input', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'constraints', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality/baseline_results/constraints.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'baseline', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-quality

INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-explainability-byom-2023-02-10-16-03-59-799



Job Name:  model-explainability-byom-2023-02-10-16-03-59-799
Inputs:  [{'InputName': 'analysis_file', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/baseline_results/analysis.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'analysis_config', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/baseline_results/analysis_config.json', 'LocalPath': '/opt/ml/processing/input/config', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'dataset', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-explainability/i

No violations file found. Maybe No violations were detected


INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating processing-job with name model-bias-byom-2023-02-10-16-40-37-896



Job Name:  model-bias-byom-2023-02-10-16-40-37-896
Inputs:  [{'InputName': 'analysis_file', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/baseline_results/analysis.json', 'LocalPath': '/opt/ml/processing/baseline/constraints', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'analysis_config', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/baseline_results/analysis_config.json', 'LocalPath': '/opt/ml/processing/input/config', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'dataset', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-eu-west-1-204040576187/model-monitor-bring-your-own-model/model-bias/input_data/model_bias_modified_data.csv',